# Transakcije v MariaDB/MySQL (transakcija A)

### Pomožni elementi 

In [1]:
# pyODBC
import pyodbc
try:
    cn1.close()
except:
    pass

# MariaDB/MySQL
conn = "DSN=tup;DATABASE=sandbox;UID=tup;PWD=tupvaje"
cn1 = pyodbc.connect(conn, autocommit=False)
c1=cn1.cursor()

In [2]:
# Izpis rezultatov poizvedbe (pomožna funkcija)
def tabela(rez):
  try:
    # Glava
    for g in rez.description:
        print(g[0],end="\t")
    print("\n"+"-"*31)
    # Vsebina
    for r in rez.fetchall():
        for a in r:
            print(a,end="\t")
        print()    
    # Število vrstic
    print("Vseh vrstic je", rez.rowcount)
  except Exception(e):
    pass

## Nadaljuj s pomožnimi elementi transakcije B

## Korak A1: nastavi transakcijske parametre za vse nadaljnje nove transakcije

In [3]:
# Timeout ob predolgem zaklepanju
c1.execute("SET SESSION innodb_lock_wait_timeout = 5") # Čas v sekundah
# Preizkusite različne stopnje izolacije
c1.execute("SET SESSION TRANSACTION ISOLATION LEVEL READ COMMITTED") 
# Začnemo novo transakcijo
c1.commit()

## Korak A2: kreiramo in napolnimo testno tabelo

In [6]:
c1.execute("DROP TABLE IF EXISTS rezervacija")
c1.execute("DROP TABLE IF EXISTS jadralec") 
c1.execute("CREATE TABLE jadralec AS SELECT * from tup.Jadralec")
c1.execute("ALTER TABLE jadralec ADD PRIMARY KEY(jid)")
#c1.execute("ALTER TABLE jadralec ENGINE MYISAM") # Privzeto: InnoDB
c1.commit();

## Korak A3: izpis vsebine tabele pred spremembo

In [7]:
c1.execute("SELECT * FROM jadralec")
tabela(c1)

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	1	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


## Nadaljuj s korakom B1

-------------------------------
# <font color='green'>Branje neobstoječega podatka (dirty read)</font>

- stopnja izolacije mora biti vsaj `READ COMMITTED`


## Korak A4: sprememba tabele

In [8]:
try:
    c1.execute("UPDATE jadralec  \
                SET rating = 7  \
                WHERE jid = 29")
except Exception as e:
    print(e)



## Korak A5: izpis vsebine tabele po spremembi

In [9]:
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	7	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


## Nadaljuj na koraku B5

## Korak A6: razveljavi spremembe in ponovno izpiši

In [10]:
c1.rollback()
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	1	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


# <font color='green'>Izgubljeno ažuriranje</font>

## Korak A7: začetek nove transakcije in izpis ratinga

In [11]:
c1.rollback()
c1.execute(""" SELECT rating  
               FROM jadralec
               WHERE jid = 29""")
rating = c1.fetchone()[0]
print (rating)

1


## Nadaljuj s korakom B4

## Korak A8: sprememba ratinga

In [12]:
c1.execute("UPDATE jadralec  \
            SET rating = ?  \
            WHERE jid = 29", rating + 1)


## Nadaljuj s korakom B5

## Korak A9: potrjevanje sprememb in izpis

In [13]:
c1.commit()
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	2	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


------
# <font color='green'>Neponovljivo branje (`non-repeatable read`)</font>
- Potrebuje stopnjo izolacije najmanj `REPEATABLE READ` 
- Alernativno: `SELECT ...  LOCK IN SHARE MODE` na kateri koli stopnji izolacije

## Korak A10: začetek transakcije in prvi izpis

In [14]:
c1.commit()
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	2	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


## Nadaljuj s korakom B7

## Korak A11: nadaljevanje transakcije in drugi izpis

In [15]:
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	2	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


---------
# <font color='green'>Fantomsko branje (`phantom read`)</font>
## Potrebujemo `SERIALIZABLE`

## Korak A12: začetek transakcije in prvi izpis

In [16]:
c1.commit()
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	2	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


## Nadaljuj s korakom B8

## Korak A13: nadaljevanje transakcije in drugi izpis

In [17]:
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	7	45.0	
29	Borut	2	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10


### Če je stopnja izolacije nižja od `SERIALIZABLE` pride do pojava fantomske vrstice.

----
# <font color='green'>Mrtva zanka<font>

## Korak A14: prva sprememba in zaklepanje

In [18]:
c1.commit()
c1.execute("SET innodb_lock_wait_timeout = 500") # Daljši timeout samo za trenutno transakcijo
c1.execute("UPDATE jadralec  \
            SET rating = ?  \
            WHERE jid = 22", 3)

## Nadaljuj s korakom B9.
## Korak A15: druga sprememba in zaklepanje

In [19]:
c1.execute("UPDATE jadralec  \
            SET rating = ?  \
            WHERE jid = 29", 8)
c1.commit()

### Čakamo na transakcijo B, dokler se ta ne prekine zaradi pojava mrtve zanke.
## Nadaljuj s korakom B10.

## Korak A16: izpis 

In [20]:
tabela(c1.execute("SELECT * FROM jadralec"))

jid	ime	rating	starost	
-------------------------------
22	Darko	3	45.0	
29	Borut	8	33.0	
31	Lojze	8	55.5	
32	Andrej	8	25.5	
58	Rajko	10	35.0	
64	Henrik	7	35.0	
71	Zdravko	10	16.0	
74	Henrik	9	35.0	
85	Anze	3	25.5	
95	Bine	3	63.5	
Vseh vrstic je 10
